# Farshid Pirahansiah
## LLMOPs 
## Building a RAG application




In [23]:
import os
from dotenv import load_dotenv
load_dotenv()
OPENAI_API_KEY = os.getenv("OPENAI_API_KEY")

from langchain.chat_models import ChatOpenAI
from langchain.schema.messages import HumanMessage, AIMessage

chain_gpt_35 = ChatOpenAI(model="gpt-3.5-turbo", max_tokens=1024)
chain_gpt_4_vision = ChatOpenAI(model="gpt-4-vision-preview", max_tokens=1024)


/Users/farshid/miniconda3/envs/rag/lib/python3.10/site-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.0.10 and will be removed in 0.2.0. An updated version of the class exists in the langchain-openai package and should be used instead. To use it run `pip install -U langchain-openai` and import as `from langchain_openai import ChatOpenAI`.
  warn_deprecated(


In [1]:

# Function for text summaries
def summarize_text(text_element):
    prompt = f"Summarize the following text:\n\n{text_element}\n\nSummary:"
    response = chain_gpt_35.invoke([HumanMessage(content=prompt)])
    return response.content

# Function for table summaries
def summarize_table(table_element):
    prompt = f"Summarize the following table:\n\n{table_element}\n\nSummary:"
    response = chain_gpt_35.invoke([HumanMessage(content=prompt)])
    return response.content

# Function for image summaries
def summarize_image(encoded_image):
    prompt = [
        AIMessage(content="You are a bot that is good at analyzing images."),
        HumanMessage(content=[
            {"type": "text", "text": "Describe the contents of this image."},
            {
                "type": "image_url",
                "image_url": {
                    "url": f"data:image/jpeg;base64,{encoded_image}"
                },
            },
        ])
    ]
    response = chain_gpt_4_vision.invoke(prompt)
    return response.content

/Users/farshid/miniconda3/envs/rag/lib/python3.10/site-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.0.10 and will be removed in 0.2.0. An updated version of the class exists in the langchain-openai package and should be used instead. To use it run `pip install -U langchain-openai` and import as `from langchain_openai import ChatOpenAI`.
  warn_deprecated(


In [3]:
from transformers import AutoModelForCausalLM, AutoTokenizer
import torch
torch_device="cuda" if torch.cuda.is_available() else "cpu"

In [4]:
model_name="mrm8488/distilroberta-finetuned-financial-news-sentiment-analysis"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model=AutoModelForCausalLM.from_pretrained(model_name,pad_token_id=tokenizer.eos_token_id).to(torch_device)


tokenizer_config.json: 100%|██████████| 333/333 [00:00<00:00, 145kB/s]
vocab.json: 100%|██████████| 798k/798k [00:14<00:00, 54.9kB/s]
merges.txt: 100%|██████████| 456k/456k [00:05<00:00, 80.4kB/s]
tokenizer.json: 100%|██████████| 1.36M/1.36M [00:16<00:00, 82.3kB/s]
config.json: 100%|██████████| 933/933 [00:00<00:00, 2.36MB/s]
model.safetensors: 100%|██████████| 328M/328M [06:42<00:00, 816kB/s] 
If you want to use `RobertaLMHeadModel` as a standalone, add `is_decoder=True.`
Some weights of RobertaForCausalLM were not initialized from the model checkpoint at mrm8488/distilroberta-finetuned-financial-news-sentiment-analysis and are newly initialized: ['lm_head.bias', 'lm_head.decoder.bias', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.layer_norm.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [5]:
model_input=tokenizer('pirahansiah.com reported profits of xxxxM',return_tensors='pt').to(torch_device)

In [7]:
output=model(**model_input).logits.argmax(axis=1)

In [9]:
output.item()

RuntimeError: a Tensor with 50265 elements cannot be converted to Scalar

In [21]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import torch

# Ensure you have the correct model
model_name = "mrm8488/distilroberta-finetuned-financial-news-sentiment-analysis"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForSequenceClassification.from_pretrained(model_name).to('cuda' if torch.cuda.is_available() else 'cpu')

# Prepare your input text
text = "pirahansiah.com reported profits only 1M while 2M profits of last year"
encoded_input = tokenizer(text, return_tensors='pt').to('cuda' if torch.cuda.is_available() else 'cpu')

# Get predictions
with torch.no_grad():
    predictions = model(**encoded_input)

# Process predictions
scores = predictions[0][0].softmax(dim=0)
labels = ['Negative', 'Neutral', 'Positive']
prediction = labels[scores.argmax().item()]

print(f"Sentiment: {prediction}")


Sentiment: Negative


# fine-tune GPT2

In [25]:
#!pip install datasets
TOKENIZERS_PARALLELISM = True
from transformers import GPT2Tokenizer, TrainingArguments, Trainer, GPT2LMHeadModel
from datasets import load_dataset
dataset=load_dataset("sst2")

In [27]:
#dataset=load_dataset("sst2")
#for row in dataset['train']:
#    print(row)
for i, row in enumerate(dataset):
    prep_txt=f"<|startoftext|> {row['sentence']}<|pad|>Sentiment:{row['label']}<|endoftext|>" 
    encodings_dict=tokenizer(prep_txt)
tokenizer = GPT2Tokenizer.from_pretrained('gpt2',bos_token='<|startoftext|>',eos_token='<|endoftext|>',pad_token='<|pad|>')


{'idx': 0, 'sentence': 'hide new secretions from the parental units ', 'label': 0}
{'idx': 1, 'sentence': 'contains no wit , only labored gags ', 'label': 0}
{'idx': 2, 'sentence': 'that loves its characters and communicates something rather beautiful about human nature ', 'label': 1}
{'idx': 3, 'sentence': 'remains utterly satisfied to remain the same throughout ', 'label': 0}
{'idx': 4, 'sentence': 'on the worst revenge-of-the-nerds clichés the filmmakers could dredge up ', 'label': 0}
{'idx': 5, 'sentence': "that 's far too tragic to merit such superficial treatment ", 'label': 0}
{'idx': 6, 'sentence': 'demonstrates that the director of such hollywood blockbusters as patriot games can still turn out a small , personal film with an emotional wallop . ', 'label': 1}
{'idx': 7, 'sentence': 'of saucy ', 'label': 1}
{'idx': 8, 'sentence': "a depressed fifteen-year-old 's suicidal poetry ", 'label': 0}
{'idx': 9, 'sentence': "are more deeply thought through than in most ` right-thinking 

TypeError: string indices must be integers

In [21]:
from transformers import GPT2Tokenizer, GPT2LMHeadModel, Trainer, TrainingArguments
from datasets import load_dataset

# Load the dataset
#dataset = load_dataset("sst2")

# Initialize tokenizer with special tokens
tokenizer = GPT2Tokenizer.from_pretrained('gpt2')
tokenizer.add_special_tokens({'bos_token': '<|startoftext|>', 'eos_token': '<|endoftext|>', 'pad_token': '<|pad|>'})

# Load the model and resize its token embeddings (due to the added special tokens)
model = GPT2LMHeadModel.from_pretrained('gpt2')
model.resize_token_embeddings(len(tokenizer))

# Define the preprocess function
def preprocess_data(examples):
    # Note: examples['sentence'] and examples['label'] are lists
    prep_texts = [f"{sentence} Sentiment: {label}" for sentence, label in zip(examples['sentence'], examples['label'])]
    return tokenizer(prep_texts, truncation=True, padding=True, max_length=512)

# Apply preprocessing and prepare the dataset
train_dataset = dataset['train'].map(preprocess_data, batched=True, remove_columns=dataset['train'].column_names)
train_dataset.set_format(type='torch', columns=['input_ids', 'attention_mask'])

# Define training arguments
training_args = TrainingArguments(
    output_dir='./results',     # The output directory for the model predictions and checkpoints
    num_train_epochs=1,         # Total number of training epochs
    warmup_steps=100,           # Number of steps used for a linear warmup from 0 to learning_rate
    weight_decay=0.01,          # Strength of weight decay
    per_device_train_batch_size=4,  # Batch size per device during training
    logging_dir='./logs',       # Directory for storing logs
)

# Initialize Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset
)

# Start training
trainer.train()


ImportError: Using the `Trainer` with `PyTorch` requires `accelerate>=0.21.0`: Please run `pip install transformers[torch]` or `pip install accelerate -U`

In [18]:
#!pip install torch torchvision torchaudio
#!pip install accelerate -U
#!pip install transformers[torch]
#!pip install 'transformers[torch]'
#!pip install 'accelerate>=0.21.0' -U
#!pip show accelerate
#!pip install --upgrade transformers
#!pip install torch torchvision torchaudio --extra-index-url https://download.pytorch.org/whl/cpu




Looking in indexes: https://pypi.org/simple, https://download.pytorch.org/whl/cpu


In [ ]:
model.eval()

prompt = f'<|startoftext|>Tweet: [text}\nSentiment:' 
tokenized_text = tokenizer (prompt, return_tensors="pt"). input_ids 
output = model.generate (tokenized_text) 
predicted_text = tokenizer. decode (output)

# Optimization LLMs for startup usage

## Why Compress LLMs

- Computationally demanding
- Long execution times
- Multi-GPU dependency

## Compression Benefits

- Enables deployment on lower-end devices
- Reduces operational costs
- Lowers memory usage
- Enhances energy efficiency
- Latency 


# Quantization
- reducing precision (F32-16,8,4,3,1)
- methods
    - weight quantization
    - weight and activation (the output of each neuron)

# Puring
- eliminating less crucial model connections
- reduction in memory usage
- speedup inference
- methods:
    -Pruning Types • Magnitude-based pruning: targeting smallest-value parameters • Structured pruning: eliminating neurons/layers based on output contribution • Real-world application: achieving 90% sparsity in AlexNet with minimal performance loss • Navigating the computational challenges of parameter identification • Innovation: exploring automated pruning algorithms for efficiency
    

In [22]:
!pip install auto-gptq

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 126.1/126.1 kB 646.1 kB/s eta 0:00:0000:0100:01
  Preparing metadata (setup.py) ... error
  error: subprocess-exited-with-error
  
  × python setup.py egg_info did not run successfully.
  │ exit code: 1
  ╰─> [6 lines of output]
      Traceback (most recent call last):
        File "<string>", line 2, in <module>
        File "<pip-setuptools-caller>", line 34, in <module>
        File "/private/var/folders/sp/2_7sybqn6_sb7dyh4pxx1hpm0000gn/T/pip-install-j_qbnxuh/auto-gptq_1851c3acf8764afd8aed4697fa8332ea/setup.py", line 62, in <module>
          CUDA_VERSION = "".join(os.environ.get("CUDA_VERSION", default_cuda_version).split("."))
      AttributeError: 'NoneType' object has no attribute 'split'
      [end of output]
  
  note: This error originates from a subprocess, and is likely not a problem with pip.
error: metadata-generation-failed

× Encountered error while generating package metadata.
╰─> See above for output.

note: This is an issue

# Prompt engineering

1. Zero-Shot Prompting

- Conceptual framework: instructing LLM without prior task-specific examples
- Analogy: expecting a knowledgeable friend to provide instant answers
- Operational dynamics: LLM taps into its broad training and innate linguistic structures
- Model behavior: relying on generalized knowledge and recognizing patterns


2. Instruction Prompting

- Definition: embedding explicit task blueprints within the prompt
- Nuances: can specify format, length, style, and more
- Applications: tailored content generation, specific audience targeting, precise output formatting
- Strategic advantage: control over output granularity, ensuring LLM's response fulfills exact criteria

3. Chain-of-Thought (CoT) Prompting

- Rationale: some LLM tasks require progressive guidance
- Implementation: sequentially structured prompts guiding the model through a thought process
- Applications: complex situations needing layered analysis, like multi-domain reasoning
- Utility: ensures a holistic and contextualized output, especially when tasks necessitate nuanced understanding

4. Self-Consistency Prompting

- Core idea: iteratively generate responses, critically evaluate, and then pick the optimal one
- Analogy: drafting multiple thesis statements before settling on the most compelling one
- Technical dynamics: LLM evaluates consistency, context adherence, and linguistic fluency
- Value proposition: maximizing the odds of obtaining a coherent, contextually apt, and refined response

# Prompt Tuning

Prompt tuning helps:

- Make outputs reliable and consistent
- Add context to get better outputs
- Reduce hallucinations

# Prompt Engineering Types

## Zero-Shot Learning or Basic Prompting
- Simple tasks
- No previous examples needed

## Instruction Prompting
- Detailed instructions
- Precision required
- Limited token budget

## Few Shot Learning
- High-quality examples provided
- Few examples needed

## Context Instruction Learning
- Demonstrations over multiple tasks

## Chain-of-Thought (CoT) Prompting
- Complex tasks
- Sequential reasoning required

## Self-Consistency Sampling
- Multiple outputs created and evaluated


In [33]:
#Zero-Shot Prompt
import time
from openai import OpenAI
client = OpenAI(
    api_key=os.environ.get("OPENAI_API_KEY"),
)
start_time=time.time()
chat_completion = client.chat.completions.create(
    messages=[
        {
            "role": "user",
            "content": "create a talk proposal for 'Large Vision Models (LVMs)'",
        }
    ],
    model="gpt-3.5-turbo",
)
total_time=time.time()-start_time

In [34]:
main_output = chat_completion.choices[0].message.content
print(main_output)
print("Total time for API call: {:.2f} seconds".format(total_time))

Title: Unleashing the Power of Large Vision Models (LVMs)

Abstract:
In recent years, there has been a paradigm shift in the field of computer vision with the advent of Large Vision Models (LVMs) that have revolutionized tasks such as image classification, object detection, and semantic segmentation. These models have shown remarkable performance, outperforming traditional computer vision algorithms and setting new benchmarks in various vision tasks. In this talk, we will delve into the world of LVMs and explore their capabilities, architectures, and applications.

Outline:
1. Introduction to Large Vision Models (LVMs)
- What are LVMs?
- Evolution of LVMs
- Key characteristics and advantages of LVMs

2. Architectures of LVMs
- Overview of popular LVM architectures (e.g., Vision Transformers, EfficientNet, ResNeXt)
- Understanding the building blocks of LVMs
- Comparison of different LVM architectures

3. Training and fine-tuning LVMs
- Data requirements and preprocessing for training L

In [35]:
original_question = "Say this is a test \\"
with open('output.txt', 'a') as file:
    file.write(original_question + '\n')
    file.write(main_output + '\n')

In [38]:
# few shot learning



# Few-Shot Prompt
# -Include examples and context in the prompt
# -Helps reduce hallucinations and increase consistency
# -Sample prompt:"Here are some examples of past talk proposals submitted by speakers:
# ‹example 1>
# ‹example 2>
# Using the above talk proposals as examples, can you create a proposal for a 30-minute talk titled
# 'Large Language Models
# for Dummies'?"

start_time=time.time()
chat_completion = client.chat.completions.create(
    messages=[
        {
            'role': 'user',
            'content': "create a talk proposal for 'Large Vision Models (LVMs)"
            "Here are some examples of past talk proposals submitted by speakers:\
            «example 1 with reasoning> <example 2 with reasoning>\
            Using the above talk proposals as examples, think step-by-step and create a proposal for a 30-minute talk titled\
            'Large Vision Models (LVMs)'. Write down the steps you took to arrive at the final talk proposal.\
            The proposal should have the following output format:\
            'title': ‹the title here>\
            'abstract': ‹the abstract here>\
            'talk_outline': ‹the outline here. It should only contain high-level topics and the time for each section.›\
            'detailed_outline': ‹Expand on the topics in the outline.›\
            'background_and_motivation': <the background for the talk topic and\
            the motivation for giving this talk now>\
            'target audience': ‹target audience here>",
        }
    ],
    model="gpt-3.5-turbo",
)
total_time=time.time()-start_time


In [39]:
main_output = chat_completion.choices[0].message.content
print(main_output)
print("Total time for API call: {:.2f} seconds".format(total_time))

Steps taken to create a talk proposal for 'Large Vision Models (LVMs)':

1. Title: Large Vision Models (LVMs)
2. Abstract: This talk will delve into the world of Large Vision Models (LVMs) and explore their impact on the field of computer vision. We will discuss the capabilities, challenges, and potential applications of LVMs in various industries.
3. Talk Outline:
   - Introduction to LVMs (5 minutes)
   - Overview of LVM architectures (5 minutes)
   - Training and optimization of LVMs (7 minutes)
   - Applications of LVMs in different industries (8 minutes)
   - Challenges and future directions in LVM research (5 minutes)
4. Detailed Outline:
   - Introduction to LVMs: Provide a brief overview of what LVMs are and why they are important in the field of computer vision.
   - Overview of LVM architectures: Discuss different architectures used in LVMs, such as convolutional neural networks (CNNs) and transformer models.
   - Training and optimization of LVMs: Explain the process of trai

In [40]:
original_question = "Say this is a test \\"
with open('output.txt', 'a') as file:
    file.write(original_question + '\n')
    file.write(main_output + '\n')